# A numba extension for cppyy / PyROOT

In [1]:
from numba import jit
import numpy as np
import time
import ROOT
import cppyy.numba_ext

x = np.arange(100).reshape(10, 10)

################ Pure Python ###############
def go_slow(a): # Function is compiled and runs in machine code
    trace = 0.0
    for i in range(a.shape[0]):
        trace += np.tanh(a[i, i])
    return a + trace

################ Numba ###############
@jit(nopython=True)
def go_fast(a): # Function is compiled and runs in machine code
    trace = 0.0
    for i in range(a.shape[0]):
        trace += np.tanh(a[i, i])
    return a + trace

################ PyROOT ###############
@jit(nopython=True)
def go_fast_pyroot(a): # Function is compiled and runs in machine code
    trace = 0.0
    for i in range(a.shape[0]):
        trace += ROOT.tanh(a[i, i])
    return a + trace


# THE FUNCTION RUNS WITH THE SAME SPEED AS FIRST
start = time.perf_counter()
go_slow(x)
end = time.perf_counter()
print("Python Function: Elapsed (1st run) = {}s".format((end - start)))

# THE FUNCTION RUNS WITH THE SAME SPEED AS FIRST EXECUTION
start = time.perf_counter()
go_slow(x)
end = time.perf_counter()
print("Python Function: Elapsed (2nd run) = {}s".format((end - start)))


# COMPILATION TIME IS INCLUDED IN THE EXECUTION TIME!
start = time.perf_counter()
go_fast(x)
end = time.perf_counter()
print("Numba Function: Elapsed (with compilation) = {}s".format((end - start)))

# NOW THE FUNCTION IS COMPILED, RE-TIME IT EXECUTING FROM CACHE
start = time.perf_counter()
go_fast(x)
end = time.perf_counter()
print("Numba Function: Elapsed (after compilation) = {}s".format((end - start)))


# DO NOT REPORT THIS... COMPILATION TIME IS INCLUDED IN THE EXECUTION TIME!
start = time.perf_counter()
go_fast_pyroot(x)
end = time.perf_counter()
print("PyROOT Function: Elapsed (with compilation) = {}s".format((end - start)))

# NOW THE FUNCTION IS COMPILED, RE-TIME IT EXECUTING FROM CACHE
start = time.perf_counter()
go_fast_pyroot(x)
end = time.perf_counter()
print("PyROOT Function: Elapsed (after compilation) = {}s".format((end - start)))

Welcome to JupyROOT 6.27/01
Python Function: Elapsed (1st run) = 0.00015600991901010275s
Python Function: Elapsed (2nd run) = 0.00010176002979278564s
Numba Function: Elapsed (with compilation) = 0.5158683219924569s
Numba Function: Elapsed (after compilation) = 5.0544971600174904e-05s
PyROOT Function: Elapsed (with compilation) = 0.21545343508478254s
PyROOT Function: Elapsed (after compilation) = 4.931003786623478e-05s


In [2]:
import ROOT
import cppyy.numba_ext
from numba import njit

@njit
def getPiOver4():
    return ROOT.TMath.PiOver4()

@njit
def getLog10(x):
    return ROOT.TMath.Log10(x)

print(getPiOver4())
print(getLog10(10.0))

0.7853981633974483
1.0


In [3]:
import ROOT
import cppyy.numba_ext
import numba
import numpy as np

ROOT.gInterpreter.Declare("""
template<typename T>
T square(T t) { return t*t; }
""")

@numba.jit(nopython=True)
def tsa(a):
    total = type(a[0])(0)
    for i in range(len(a)):
        total += ROOT.square(a[i])
    return total
a = np.array(range(10), dtype=np.float32)
print(tsa(a))

a = np.array(range(10), dtype=np.int64)
print(tsa(a))

285.0
285


In [4]:
import ROOT
import numba
import numpy as np

ROOT.gInterpreter.Declare("""\
class MyData {
public:
    MyData(int i, int j) : fField1(i), fField2(j) {}

public:
    int get_field1() { return fField1; }
    int get_field2() { return fField2; }

    MyData copy() { return *this; }

public:
    int fField1;
    int fField2;
};""")

@numba.jit(nopython=True)
def tsdf(a, d):
    total = type(a[0])(0)
    for i in range(len(a)):
        total += a[i] + d.fField1 + d.fField2
    return total

d = ROOT.MyData(5, 6)
a = np.array(range(10), dtype=np.int32)
print(tsdf(a, d))

# example of method calls
@numba.jit(nopython=True)
def tsdm(a, d):
    total = type(a[0])(0)
    for i in range(len(a)):
        total += a[i] +  d.get_field1() + d.get_field2()
    return total

print(tsdm(a, d))

# example of object return by-value
@numba.jit(nopython=True)
def tsdcm(a, d):
    total = type(a[0])(0)
    for i in range(len(a)):
        total += a[i] + d.copy().fField1 + d.get_field2()
    return total

print(tsdcm(a, d))

155
155
155
